In [1]:
import openai
import json
import os
import polars as pl
from polars import DataFrame
from config import OPENAI_API_KEY, logger
from rag import get_examples, generate_embeddings

from dotenv import load_dotenv
from urllib.parse import urlparse
import sqlparse
from sqlparse.tokens import DML, DDL
from sqlalchemy import create_engine, text
from sqlalchemy.exc import SQLAlchemyError

load_dotenv()

tmpPostgres = urlparse(os.getenv("DATABASE_URL"))

# Создаем движок с использованием пула соединений
engine = create_engine(
    f"postgresql://{tmpPostgres.username}:{tmpPostgres.password}@{tmpPostgres.hostname}{tmpPostgres.path}?sslmode=require",
    echo=True,
    pool_pre_ping=True  # Проверяет соединение перед использованием
)


In [10]:
def get_warehouse_names() -> list[str]:
    query = text('select name from warehouse')
    try:
        with engine.connect() as conn:
            result = conn.execute(query, {"table_name": 'warehouse'})
            names = result.fetchall()
            return [a[0] for a in names]
    except SQLAlchemyError as e:
        logger.error(f"Ошибка при получении названий столбцов для таблицы warehouse: {e}")
        return []


In [12]:
a = get_warehouse_names()
print(a)

2025-01-06 11:15:04,782 INFO sqlalchemy.engine.Engine BEGIN (implicit)


2025-01-06 11:15:04,782 - sqlalchemy.engine.Engine - INFO - BEGIN (implicit)


2025-01-06 11:15:04,783 INFO sqlalchemy.engine.Engine select name from warehouse


2025-01-06 11:15:04,783 - sqlalchemy.engine.Engine - INFO - select name from warehouse


2025-01-06 11:15:04,784 INFO sqlalchemy.engine.Engine [cached since 137.8s ago] {}


2025-01-06 11:15:04,784 - sqlalchemy.engine.Engine - INFO - [cached since 137.8s ago] {}


2025-01-06 11:15:04,952 INFO sqlalchemy.engine.Engine ROLLBACK


2025-01-06 11:15:04,952 - sqlalchemy.engine.Engine - INFO - ROLLBACK


['крышка багажника, багажник, хлопушка', 'бампер зад', 'бампер перед', 'барабан тормозной', 'Бардачок', 'Бачок гидроусилителя', 'бензанос калининград', 'бензонасос Америка', 'Бензонасос Корея +дорест', 'блок абс', 'Блок предохранителей', 'блок упр печкой', 'блок эсп', 'вакуумник', 'вискомуфта', 'выпускной коллектор', 'генератор', 'глушитель Банка', 'глушитель средняя часть', 'глушитель хвостовик', 'Горловина топливного бака', 'Гофра воздуховода', 'гтц алюминь', 'гтц чугун', 'Датчик детонации', 'Датчик положения коленвала', 'Датчик положения распредвала', 'Датчик температуры', 'дверь зад', 'дверь перед', 'двигатель', 'диски тормозные', 'дмрв аналог', 'дмрв оригинал', 'жгут на катушки', 'заднее крыло', 'заднее стекло', 'задний дворник мотор дорест', 'задний дворник мотор рестайл', 'замок багажника дорест', 'замок багажника обычный', 'замок багажника открывающийся ручкой', 'замок зажигания', 'Замок капота', 'Защита картера', 'зеркало без обогрева', 'зеркало с обогревом', 'Испаритель конди

In [13]:
emb = generate_embeddings(a)

2025-01-06 11:15:27,321 - httpx - INFO - HTTP Request: POST https://api.openai.com/v1/embeddings "HTTP/1.1 200 OK"


['крышка багажника, багажник, хлопушка', 'бампер зад', 'бампер перед', 'барабан тормозной', 'Бардачок', 'Бачок гидроусилителя', 'бензанос калининград', 'бензонасос Америка', 'Бензонасос Корея +дорест', 'блок абс', 'Блок предохранителей', 'блок упр печкой', 'блок эсп', 'вакуумник', 'вискомуфта', 'выпускной коллектор', 'генератор', 'глушитель Банка', 'глушитель средняя часть', 'глушитель хвостовик', 'Горловина топливного бака', 'Гофра воздуховода', 'гтц алюминь', 'гтц чугун', 'Датчик детонации', 'Датчик положения коленвала', 'Датчик положения распредвала', 'Датчик температуры', 'дверь зад', 'дверь перед', 'двигатель', 'диски тормозные', 'дмрв аналог', 'дмрв оригинал', 'жгут на катушки', 'заднее крыло', 'заднее стекло', 'задний дворник мотор дорест', 'задний дворник мотор рестайл', 'замок багажника дорест', 'замок багажника обычный', 'замок багажника открывающийся ручкой', 'замок зажигания', 'Замок капота', 'Защита картера', 'зеркало без обогрева', 'зеркало с обогревом', 'Испаритель конди

In [14]:
emb

[[0.003923024516552687,
  -0.02646118588745594,
  -0.041394319385290146,
  0.003961485810577869,
  -0.0020166398026049137,
  -0.07794768363237381,
  0.03234828636050224,
  0.014420321211218834,
  0.027815014123916626,
  -0.06063508987426758,
  -0.017312590032815933,
  0.012328040786087513,
  -0.0011737023014575243,
  -0.010963956825435162,
  -0.03273802623152733,
  0.0461532324552536,
  -0.024102242663502693,
  -0.0009653717861510813,
  -0.06063508987426758,
  0.002070485381409526,
  0.025332996621727943,
  0.010087044909596443,
  0.030953435227274895,
  -0.01637926883995533,
  0.005789666436612606,
  -0.01518954150378704,
  0.018984362483024597,
  -0.06576322764158249,
  0.02063562348484993,
  -0.01993819698691368,
  0.0038409745320677757,
  -0.03269699960947037,
  0.0601838156580925,
  -0.032184187322854996,
  0.030748309567570686,
  0.014697240665555,
  -0.009035777300596237,
  -0.0228099524974823,
  0.02379455603659153,
  0.020892029628157616,
  -0.0007044778321869671,
  0.01132292